In [49]:
import pandas as pd #nul
import numpy as np
import datetime as dt
import matplotlib.pyplot as plt
import json
import geopandas as gpd
from tool_function import *
import altair as alt
from altair import expr, datum
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [51]:
#Sklearn
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import LogisticRegressionCV
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn import svm
from sklearn.inspection import permutation_importance
from sklearn.decomposition import PCA
from sklearn.pipeline import make_pipeline
from sklearn.manifold import TSNE
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.metrics import RocCurveDisplay
from sklearn.base import clone
from sklearn import linear_model

# Data Prep

In [52]:
mutations = pd.read_pickle('../../data_mutation/geometric_mutations.pkl')

In [53]:
mutations = mutation_process(mutations)
mutations = niveau_center_connexion(mutations)

hi!


In [179]:
# We only want newly built
# mutations = mutations[mutations.libnatmut.isin(["Vente en l'état futur d'achèvement", 'Vente'])].copy()
# REMOVE ALL THESE !! the no surface and no one maison/apt etc; 12% !!

df_surf = mutations[~((mutations.sbati ==0) & (mutations[['nblocmai', 'nblocapt', 'nblocact']].sum(axis=1) == 0))]
df_surf = df_surf.copy()
df_surf['smoymai'] = df_surf.sbatmai/df_surf.nblocmai
df_surf['smoyapt'] = df_surf.sbatapt/df_surf.nblocapt
df_surf['smoyact'] = df_surf.sbatact/df_surf.nblocact

df_surf.loc[df_surf['sbati'] == 0, 'sbatmai'] = df_surf.groupby('l_codinsee')['smoymai'].transform(np.nanmedian) * df_surf.nblocmai
df_surf.loc[df_surf['sbati'] == 0, 'sbatapt'] = df_surf.groupby('l_codinsee')['smoyapt'].transform(np.nanmedian) * df_surf.nblocapt
df_surf.loc[df_surf['sbati'] == 0, 'sbatact'] = df_surf.groupby('l_codinsee')['smoyact'].transform(np.nanmedian) * df_surf.nblocact

df_surf.loc[df_surf['sbati'] == 0, 'sbati'] = df_surf[['sbatmai', 'sbatapt', 'sbatact']].sum(axis=1)

df_surf.loc[df_surf['sbati'] == 0, 'sbatmai'] = df_surf.groupby('coddep')['smoymai'].transform(np.nanmedian) * df_surf.nblocmai
df_surf.loc[df_surf['sbati'] == 0, 'sbatapt'] = df_surf.groupby('coddep')['smoyapt'].transform(np.nanmedian) * df_surf.nblocapt
df_surf.loc[df_surf['sbati'] == 0, 'sbatact'] = df_surf.groupby('coddep')['smoyact'].transform(np.nanmedian) * df_surf.nblocact

df_surf.loc[df_surf.sbati == 0, 'sbati'] = df_surf[['sbatmai', 'sbatapt', 'sbatact']].sum(axis=1)

df_surf['smoymai'] = df_surf.sbatmai/df_surf.nblocmai
df_surf['smoyapt'] = df_surf.sbatapt/df_surf.nblocapt
df_surf['smoyact'] = df_surf.sbatact/df_surf.nblocact

mutations = df_surf.copy()


#We only want appartements
# mutations_apt = mutations[(mutations.nblocmai == 0) & 
# (mutations.nblocdep == 0) &
# (mutations.nblocact == 0) &
# (mutations.nblocapt > 0) ].copy()

#'libtypbien' to erase?
#'first_idpar' to erase?
mutations_apt = mutations[
  ['idmutation', 'idmutinvar', 'idopendata', 'idnatmut', 
      'datemut', 'coddep', 'libnatmut', 'vefa', 'valeurfonc',
       'nbdispo', 'nblot', 'nbcomm', 'l_codinsee', 
       'nbpar', 'nbparmut', 'nbsuf', 'sterr', 'sbati',
       'nbvolmut', 'nblocmut', 'nblocapt',
       'nbapt1pp', 'nbapt2pp', 'nbapt3pp', 'nbapt4pp',
       'nbapt5pp', 'sbatapt', 'sapt1pp', 'sapt2pp',
       'sapt3pp', 'sapt4pp', 'sapt5pp', 
       'codtypbien', 'department_code', 'libtypbien',
       'month', 'year', 'day',
       'nivcentr']
       ].copy()

#remove rows with a valeurfonc lower than 5k? 
mutations_apt = mutations_apt[mutations_apt.valeurfonc > 5000].copy()

KeyboardInterrupt: 

In [172]:
muta_surf = mutations[~((mutations.sbati ==0) & (mutations[['nblocmai', 'nblocapt', 'nblocact']].sum(axis=1) == 0))]

In [177]:
df_surf = muta_surf.copy()
df_surf['smoymai'] = df_surf.sbatmai/df_surf.nblocmai
df_surf['smoyapt'] = df_surf.sbatapt/df_surf.nblocapt
df_surf['smoyact'] = df_surf.sbatact/df_surf.nblocact

df_surf.loc[df_surf['sbati'] == 0, 'sbatmai'] = df_surf.groupby('l_codinsee')['smoymai'].transform(np.nanmedian) * df_surf.nblocmai
df_surf.loc[df_surf['sbati'] == 0, 'sbatapt'] = df_surf.groupby('l_codinsee')['smoyapt'].transform(np.nanmedian) * df_surf.nblocapt
df_surf.loc[df_surf['sbati'] == 0, 'sbatact'] = df_surf.groupby('l_codinsee')['smoyact'].transform(np.nanmedian) * df_surf.nblocact

df_surf.loc[df_surf['sbati'] == 0, 'sbati'] = df_surf[['sbatmai', 'sbatapt', 'sbatact']].sum(axis=1)

df_surf.loc[df_surf['sbati'] == 0, 'sbatmai'] = df_surf.groupby('coddep')['smoymai'].transform(np.nanmedian) * df_surf.nblocmai
df_surf.loc[df_surf['sbati'] == 0, 'sbatapt'] = df_surf.groupby('coddep')['smoyapt'].transform(np.nanmedian) * df_surf.nblocapt
df_surf.loc[df_surf['sbati'] == 0, 'sbatact'] = df_surf.groupby('coddep')['smoyact'].transform(np.nanmedian) * df_surf.nblocact

df_surf.loc[df_surf.sbati == 0, 'sbati'] = df_surf[['sbatmai', 'sbatapt', 'sbatact']].sum(axis=1)


2


In [170]:
df_surf.groupby('l_codinsee')['smoymai'].transform(np.nanmedian).loc[df_surf.sbati==0]

18         116.0
19         124.5
65          86.0
70         134.0
75          80.0
           ...  
1271362     80.0
1271383     75.0
1271496     85.0
1271501     80.0
1271544     76.0
Name: smoymai, Length: 83384, dtype: float64

In [178]:
df_surf[df_surf.sbati==0]#[['nblocmai', 'nblocapt', 'nblocdep', 'nblocact']]

Empty GeoDataFrame
Columns: [idmutation, idmutinvar, idopendata, idnatmut, codservch, refdoc, datemut, coddep, libnatmut, vefa, valeurfonc, nbdispo, nblot, nbcomm, l_codinsee, nbsection, l_section, nbpar, l_idpar, nbparmut, l_idparmut, nbsuf, sterr, nbvolmut, nblocmut, l_idlocmut, nblocmai, nblocapt, nblocdep, nblocact, nbapt1pp, nbapt2pp, nbapt3pp, nbapt4pp, nbapt5pp, nbmai1pp, nbmai2pp, nbmai3pp, nbmai4pp, nbmai5pp, sbati, sbatmai, sbatapt, sbatact, sapt1pp, sapt2pp, sapt3pp, sapt4pp, sapt5pp, smai1pp, smai2pp, smai3pp, smai4pp, smai5pp, codtypbien, libtypbien, department_code, first_idpar, geometry, centroid, month, year, day, nivcentr, smoymai, smoyapt, smoyact]
Index: []

[0 rows x 67 columns]

In [144]:
df_surf.loc[df_surf.sbati == 0, :].shape

(79637, 67)

In [133]:
df_surf.loc[df_surf.sbati == 0, 'sbati'] = df_surf[['sbatmai_c', 'sbatapt_c', 'sbatact_c']].sum(axis=1)

In [135]:
df_surf.loc[df_surf.sbati == 0, 'sbati'] = df_surf[['sbatmai_c', 'sbatapt_c', 'sbatact_c']].sum(axis=1)

In [ ]:
def combler_surface(x, col, grp):
    typ_col = col[4:]
    if  x['nbloc'+typ_col] == 0:
        return 0
    val = x['nbloc'+typ_col] * grp[(grp.l_codinsee == x.l_codinsee)]['smoy'+typ_col].values[0]
    return val

df_surf['sbatmai'] = df_surf.apply(lambda x: combler_surface(x, 'sbatmai', grp), axis=1)

In [14]:
#average surface per commune
no_s_no_nb.loc[no_s_no_nb['sbati'] == 0, 'sbati'] = no_s_no_nb.groupby('l_codinsee')['sbati'].transform(np.nanmedian)

In [16]:
no_s_no_nb.groupby('l_codinsee')['sbati'].transform('median')

Series([], Name: sbati, dtype: float64)

In [82]:
# create a sample dataframe
df = pd.DataFrame({'group': ['A', 'A', 'B', 'B', 'B', 'A'], 'value': [1, 2, 3, 0, 0, 0]})

In [83]:
df

group  value
0     A      1
1     A      2
2     B      3
3     B      0
4     B      0
5     A      0

In [96]:

# group the dataframe by 'group' column and calculate the median of each group
grouped_medians = df.groupby('group')['value'].transform(np.nanmedian)

In [102]:
df.loc[df.value==0,:]

group  value
3     B      0
4     B      0
5     A      0

In [107]:

# replace zeros in 'value' column with the corresponding median of each group
df.loc[df.value==0,'test'] = grouped_medians * df.value

print(df)

  group  value  test
0     A      1   NaN
1     A      2   NaN
2     B      3   NaN
3     B      0   0.0
4     B      0   0.0
5     A      0   0.0


In [ ]:
# filling the 0s surfaces
mutations_apt.loc[mutations_apt['sbati'] == 0, 'salary'] = df.groupby('product')['salary'].transform('median')

In [25]:
mutations[mutations.sbati ==0][['nblocmai', 'nblocapt', 'nblocdep', 'nblocact']].sum(axis=1)

0          0.0
1          0.0
3          0.0
5          0.0
6          0.0
          ... 
1271544    1.0
1271550    0.0
1271552    0.0
1271556    0.0
1271565    0.0
Length: 240505, dtype: float64

In [29]:
no_s_no_nb = mutations[(mutations.sbati ==0) & (mutations[['nblocmai', 'nblocapt', 'nblocdep', 'nblocact']].sum(axis=1) == 0)]

In [32]:
no_s_no_nb.libtypbien.value_counts()

BATI - INDETERMINE : Vefa sans descriptif    89302
TERRAIN DE TYPE TAB                          22544
TERRAIN ARTIFICIALISE MIXTE                  16513
TERRAIN DE TYPE TERRE ET PRE                  9990
TERRAIN D'AGREMENT                            5836
BATI - INDETERMINE : Vente avec volume(s)     4490
TERRAIN FORESTIER                             4038
TERRAIN NON BATIS INDETERMINE                 2458
TERRAIN VERGER                                1849
TERRAIN LANDES ET EAUX                         507
TERRAIN NATUREL MIXTE                           81
TERRAIN DE TYPE RESEAU                          56
TERRAIN VITICOLE                                43
TERRAIN D'EXTRACTION                            33
TERRAIN AGRICOLE MIXTE                          23
Name: libtypbien, dtype: int64

In [33]:
mutations[mutations.libtypbien == 'BATI - INDETERMINE : Vefa sans descriptif'].sbati.value_counts()

0.0    89302
Name: sbati, dtype: int64

In [9]:
sample_df = mutations_apt.sample(n=5000)

In [10]:
sample_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5000 entries, 1203579 to 193281
Data columns (total 39 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   idmutation       5000 non-null   float64       
 1   idmutinvar       5000 non-null   object        
 2   idopendata       5000 non-null   object        
 3   idnatmut         5000 non-null   float64       
 4   datemut          5000 non-null   datetime64[ns]
 5   coddep           5000 non-null   float64       
 6   libnatmut        5000 non-null   object        
 7   vefa             5000 non-null   bool          
 8   valeurfonc       5000 non-null   float64       
 9   nbdispo          5000 non-null   float64       
 10  nblot            5000 non-null   float64       
 11  nbcomm           5000 non-null   float64       
 12  l_codinsee       5000 non-null   object        
 13  nbpar            5000 non-null   float64       
 14  nbparmut         5000 non-null  

In [15]:
sample_df[sample_df.sbatapt< 10]

idmutation                        idmutinvar  \
341289   6933515.0  a4a2ae914b71e9bc50d5a1c5795d175e   
222762   6807017.0  073e61685bf4c99f7c1c8a99bc4fdc3b   
314300   6672462.0  4b6f314f489331a4a2714367995f77aa   
248232   6366214.0  e812129fbf47f211d56a782e0a87a0b1   
207567   6513718.0  8ab2c2cc1f65ec1e3183e39f35582dca   
166959   6802859.0  0514344a9f2f6adc4197c6f4c164cc64   
307724   6245798.0  9554ef62287a2218bf2048d81d7ae11c   
295168   6668301.0  437685938c673101d32d78123d5f2104   
368588   6810092.0  8346f4e014dd1693f2e31d5f72ed71f5   
377863   6356583.0  43ff4592b2539fc0987d899c7ccda800   
270474   6529159.0  0f20e9f3d75f396c481c85c5c0c5dbd2   
299344   6531011.0  b74a50a9bb0dd4c9f32138925b2ad591   
198332   6538784.0  13ef6448630ede3f134d8155c324f20e   
336474   6945412.0  1f1453aefeba21536f9f487c36e39c41   
311221   6239167.0  88dc630bad3c9d61d9a58c06590f433e   
371574   7078192.0  d3eb828ea9425bf684fce7f978dc9908   
322020   7068095.0  cd009e6c3dc80d43269282d73df1d12f   
302936   6354466.0  816f6d454c400c354e46a36c6498a10b   
316535   7073430.0  daf66413020e10ef9b987df1c4804744   
295715   6695183.0  06e01075c7ed3fa0e2658bfae38d3059   
381048   6661185.0  958d668b38c1dea3c3ef521c9a4c8ea4   
704585   8163308.0  7eb0eee08483b24d4fb06bf5ed198a38   
350033   6661260.0  bc71bc78c3dfdf71a98a346463b2a4b6   
218238   6525231.0  5a55b87d886fa91bd91e509a9a077300   
187213   6835487.0  1ecbafe908cddf6e51a6e8dfaa745126   
173760   6530424.0  6a54df42458c0a145a0d146f54038856   
204699   6832363.0  e0856782260e6c5375c66dcd5fe6fbf0   
366885   6959168.0  b95f329347b69da858f290c30df1823b   
195546   7063845.0  ff2ce2923662fcdd93d052aa47a6cc54   
224537   6381140.0  12251091509742cba4289318552e0371   
320399   6941546.0  9d8a001339ed0315606f77b7ebd66f59   
303076   6663726.0  e56067c81a87ec39629cb7e1bebcb094   
212392   6362333.0  26ad6277ced978b8f29ae212da66ec48   
292967   6665547.0  1adab908876301ca2674467ab4685149   
272614   6389232.0  7ce69756d40da98d0c7bd311f97148d3   
372009   6511915.0  2f22b0d5c7222054831663a13dbf9417   
795007   8174967.0  8d6d3effc7379ad743b14fab6b0d5240   
784697   8157482.0  cc168c4a82a12385bfb6146901cd75c2   
827292   8066916.0  2f8e59f9b31ea500ea044e7f01c85dd3   
370407   7056850.0  edba12dbd92e143d17ea8dbfbc473be0   
379818   6662689.0  d5703c4264ab09f9b3f4491d33c2f0d8   
301023   6818393.0  ea0b77251b280090a00bf74d8e603480   
277965   6383082.0  c1fd4d9f1da52824f834ca1a1f7b72ab   
157648   6546176.0  ddb989b99fbf6ba3f81b852b9b82ff20   

                              idopendata  idnatmut    datemut  coddep  \
341289  a4a2ae914b71e9bc50d5a1c5795d175e       1.0 2015-12-01    75.0   
222762  073e61685bf4c99f7c1c8a99bc4fdc3b       1.0 2016-09-01    75.0   
314300  4b6f314f489331a4a2714367995f77aa       1.0 2017-03-01    75.0   
248232  e812129fbf47f211d56a782e0a87a0b1       1.0 2019-08-01    75.0   
207567  8ab2c2cc1f65ec1e3183e39f35582dca       1.0 2018-05-01    75.0   
166959  0514344a9f2f6adc4197c6f4c164cc64       1.0 2016-12-01    75.0   
307724  9554ef62287a2218bf2048d81d7ae11c       1.0 2020-11-01    75.0   
295168  437685938c673101d32d78123d5f2104       1.0 2017-02-01    75.0   
368588  8346f4e014dd1693f2e31d5f72ed71f5       1.0 2016-11-01    75.0   
377863  43ff4592b2539fc0987d899c7ccda800       1.0 2019-10-01    75.0   
270474  0f20e9f3d75f396c481c85c5c0c5dbd2       1.0 2018-09-01    75.0   
299344  b74a50a9bb0dd4c9f32138925b2ad591       1.0 2018-11-01    75.0   
198332  13ef6448630ede3f134d8155c324f20e       1.0 2018-03-01    75.0   
336474  1f1453aefeba21536f9f487c36e39c41       1.0 2015-07-01    75.0   
311221  88dc630bad3c9d61d9a58c06590f433e       1.0 2020-02-01    75.0   
371574  d3eb828ea9425bf684fce7f978dc9908       1.0 2014-07-01    75.0   
322020  cd009e6c3dc80d43269282d73df1d12f       1.0 2014-07-01    75.0   
302936  816f6d454c400c354e46a36c6498a10b       1.0 2019-06-01    75.0   
316535  daf66413020e10ef9b987df1c4804744       1.0 2014-09-01    75.0   
295715  06e01075c7ed3fa0e26

In [11]:
sample_df['datemut'] = sample_df.datemut.dt.to_period('M').dt.to_timestamp()
sample_df['price_per_apt'] = sample_df.valeurfonc/sample_df.nblocapt

alt.Chart(sample_df).mark_line().encode(
    x='datemut:T',
    y='mean(price_per_apt):Q',
    color='department_code:N'
)

alt.Chart(...)

In [16]:
alt.Chart(sample_df).mark_bar().encode(
    x=alt.X('nivcentr'),
    y='count():Q',
    color='department_code:N'
)

alt.Chart(...)

In [ ]:
alt.Chart(sample_df).mark_point().encode(
    x=alt.X('nivcentr'),
    y='',
    color='department_code:N'
)

In [ ]:
sample_df

# Mutation ARIMA

In [ ]:
from statsmodels.tsa.api import SARIMAX, AutoReg
from statsmodels.tsa.arima.model import ARIMA

In [ ]:
mutations_arima = mutations_apt[[
    'idmutation', 'datemut',  'month', 'year', 'day', 'valeurfonc', 'department_code', 'sbatapt', 'sbati', 'nblocapt'
]].copy()
mutations_arima['datemut'] = mutations_arima.datemut.dt.to_period('M').dt.to_timestamp()
mutations_arima['price_per_apt'] = mutations_arima.valeurfonc/mutations_arima.nblocapt

In [ ]:
# arim_grp = mutations_arima.groupby(['department_code', 'datemut']).agg({'price_per_apt': 'mean'}).reset_index()
alt.Chart(mutations_arima).mark_line().encode(
    x='datemut:T',
    y='mean(price_per_apt):Q',
    color='department_code:N'
)

# Separate X and Y

In [ ]:
X = mutations_apt[[
    'idmutation', 
      'datemut', 'coddep', 'libnatmut', 'vefa',
       'nbdispo', 'nblot', 'nbcomm', 'l_codinsee', 
       'nbpar', 'nbparmut', 'nbsuf', 'sterr',
       'nbvolmut', 'nblocmut', 'nblocapt',
       'nbapt1pp', 'nbapt2pp', 'nbapt3pp', 'nbapt4pp',
       'nbapt5pp', 'sbatapt', 'sapt1pp', 'sapt2pp',
       'sapt3pp', 'sapt4pp', 'sapt5pp', 
       'codtypbien', 'department_code', 'libtypbien',
       'month', 'year', 'day',
       'nivcentr'
]].copy()
Y = mutations_apt[['valeurfonc']].copy()
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.33, random_state=42)

In [ ]:
ohe = OneHotEncoder(handle_unknown='ignore').fit(X_train)
scalery = StandardScaler().fit(y_train)
# y_train = scalery.transform(y_train)
# scalery.inverse_transform(scalery.transform(y_train))

In [ ]:
scalery.inverse_transform(scalery.transform(y_train))

In [ ]:
y_train

In [ ]:
clf_lin = linear_model.SGDRegressor(loss='squared_error', penalty=None, random_state=42) 
pipeline_lin = make_pipeline(ohe, clf_lin)

In [ ]:
pipeline_lin.fit(X_train, y_train)

In [ ]:
pred = pipeline_lin.predict(X_test)

In [ ]:
inv_pred = scalery.inverse_transform([pred])

In [ ]:
mean_squared_error(inv_pred.ravel(), y_test)

In [ ]:
inv_pred

In [ ]:
y_test['pred'] = pred.ravel()

In [ ]:
y_test